In [0]:
%run ../_utils

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
from pyspark.sql.functions import (
    col,
    count,
    date_diff,
    lit,
    min,
    count,
    sum,
    sqrt,
    when,
    concat
)
from datetime import date


# RFV

RFV, ou Recency, Frequency, and Value, é uma técnica de análise de dados frequentemente usada em marketing e gerenciamento de clientes para segmentar clientes com base em seu comportamento de compra.

Essa abordagem analisa três aspectos principais do comportamento do cliente:

- **Recency (Recência):** Refere-se à última vez que um cliente fez uma compra. Geralmente, clientes que fizeram compras recentes são mais propensos a fazer compras futuras do que aqueles que não compraram há muito tempo.
- **Frequency (Frequência):** Refere-se à frequência com que um cliente faz compras durante um determinado período de tempo. Clientes que compram com frequência podem ser considerados mais leais e valiosos para a empresa.
- **Value (Valor):** Refere-se ao valor monetário total das compras feitas por um cliente durante um determinado período de tempo. Clientes que gastam mais têm um valor de vida do cliente mais alto e podem ser alvos de estratégias de marketing mais agressivas.

Ao analisar esses três aspectos juntos, as empresas podem segmentar seus clientes em diferentes grupos com base em seu comportamento de compra e adaptar suas estratégias de marketing e relacionamento com o cliente de acordo. Por exemplo, clientes com alta recência, frequência e valor podem ser segmentados como clientes VIP e receber ofertas exclusivas, enquanto clientes com baixa recência, frequência e valor podem ser alvos de campanhas de reativação.

----

## Implementação

 - **1 Calcular a Recency (Recência):** Determinar a última data de compra para cada cliente.
 - **2 Calcular a Frequency (Frequência):** Contar o número de transações que cada cliente realizou durante um determinado período de tempo.
 - **3 Calcular o Value (Valor):** Calcular o valor total gasto por cada cliente durante o mesmo período de tempo.
 - **4 Atribuir Pontuações:** Atribuir pontuações a cada cliente com base nos três aspectos (Recency, Frequency, Value).
- **5 Segmentação de Clientes:** Segmentar os clientes com base nas pontuações atribuídas.


In [0]:
tb_name = "olist_gold.customers_rfv"
dataset_location = "olist_customers_rfv_dataset"
target_location = f"dbfs:/FileStore/delta/brazilian_ecommerce/{dataset_location}/gold"

## 1 - Data ingestion


In [0]:
df_customers = spark.sql("SELECT customer_id, customer_unique_id, customer_state FROM olist_silver.customers")

df_orders = spark.sql("SELECT order_id, customer_id, DATE(order_purchase_timestamp) as order_date FROM olist_silver.orders")

# dados de order items cruzados com products para trazermos a categoria do produto
df_order_items =spark.sql("""SELECT 
                          order_id, l.product_id, product_category_name  
                          FROM olist_silver.order_items l 
                          INNER JOIN olist_silver.products r
                          ON l.product_id = r.product_id
                          """)

df_order_payments = spark.sql("SELECT order_id, payment_value FROM olist_silver.order_payments")


## 2 - preparation

In [0]:
date_pd = df_orders.select("order_date").toPandas()

MIN_DATE = date_pd.min()[0]
MAX_DATE = date_pd.max()[0]

print(f'''
Analysis init date: {MIN_DATE}
 Analysis end date: {MAX_DATE}
  Days of analysis: {(MAX_DATE - MIN_DATE).days}
''')


Analysis init date: 2016-09-04
 Analysis end date: 2018-10-17
  Days of analysis: 773




## Joins

In [0]:
df = (
    df_orders
    .join(df_order_payments, on="order_id", how="left")
    .join(df_customers, on="customer_id", how="left")
    .filter(col("payment_value").isNotNull() & col("customer_state").isNotNull())
    .withColumn("time_since_last_order", date_diff(lit(MAX_DATE), col("order_date")))
)


### RFV

In [0]:
df = (
    df
    .groupBy("customer_unique_id")
    .agg(
        min("time_since_last_order").alias("recency"), # tempo da ultima compra
        count("order_id").alias("frequency"), # frequencia de compra
        sum("payment_value").alias("value") # valor total de gastos
    )
)

In [0]:
display(df)

customer_unique_id recency frequency value 969cdc8af5b07074766e79c1e6d76c24 163 1 134.66 f2a9bc9a1db05c873e1419654f747f9e 78 1 122.42 d0c5e56e04e886e73c79b3b71f0d6f0b 466 1 79.24 5f03b965e26e79a371d229cfeeb578d7 484 1 54.0 14a188558af6cd5bc222ca773d395a7f 224 2 245.14999999999998 ef1c2fafea5285a4bfb61386bc5e3154 58 1 235.84 d339ed835c9d8fd6b1e3c5cb60850bc5 614 1 262.1 39d6e50625a51a618c2cf02a026231c1 433 1 66.74 8d2fa65d968da66afc05f2e28250c9dc 225 1 150.91 d04921557f1cde4963c30a11dfb1719d 55 1 155.98 8033f408bcb75134075db3eb60b49937 432 2 130.0 9ea65227cfac84dd2778bc0315dd8f10 55 1 119.79 2a6ef69674d6f28002c72b8d123b3a27 208 1 32.69 308dfe5168e217902973b27e7c91f27e 93 1 117.79 1d2435aa3b858d45c707c9fc25e18779 638 16 147.58 538f20c5da86daf31ec285792b8b603f 468 1 72.84 968436577c1e2073b28031261cb45a24 286 1 91.26 1843cceebcc1e391249a2714facc8ba3 162 1 99.43 86669cc06c6e824b3f2edfc2daef762e 111 1 61.36 c114c44566c2d172b520bc3c8785ffdf 526 1 1234.62 f13f6afa0bcce14330a5bcb6f1076904 119 1 236.07 8c2c7fb3be4fc1669b8c1c6059db1207 522 1 41.91 384ffc528dd30fd49eff3dda9f00ce86 173 1 61.69 10aa79627a28350b5c121a124096cb18 470 1 46.01 19fe66d478bfedfdcc743014d562b777 127 1 56.97 09976ab240099cc26220384fa752e4f1 198 1 91.82 e2fa02776abcbf7246ffd18f58e120ea 588 1 189.62 dfe634d4b8e0678799178b6ec8e1b0ba 94 1 85.58 61bf8e4656ece5791021786c756f1894 105 1 241.95 65be6248a39942f9ab10da91280e2576 93 1 64.91 7d27012b117e625faff580bec7cdf2e1 239 1 194.64 d242c2a33b19c5fab2ccf4f67dcaba86 163 1 397.7 f43b5eb3178b2129b9c4ea51024fcbd9 201 1 61.79 39735e754fd0147ac6b0b910b710e6de 233 1 95.22 aadd69366d3b2ff8d40da4f079a4fcf7 266 1 109.5 90c329efbf418634b40f4a2a75d9331e 428 1 240.76 f1eb09d2858a28f796484f8a9dfe2872 388 1 93.3 04ebe7670da121a91344d0fd5547222f 255 1 31.28 dddcc50cec9aabfe44b26c136236db0a 427 1 176.78 8b6afb5c9eb182373c656b34bf3383fc 603 1 30.75 3195d6c23c9f61b0bcfae41d3fe8a3db 128 1 106.5 9eedcaf541a8a393248b2017afecf694 370 1 149.7 8e61d2d055f4865036e7d62b6739c255 134 1 77.99 30cd4e5146e6f7b12f08bacaec791418 130 1 76.12 02bab436d042d111ec4b7c67cfab8835 75 1 145.94 1973beff39565594011f9a0ef66f923e 391 1 218.16 1a6c2d0ed3299790cb718bb7981558c7 70 1 62.02 1234ccd4e0b359525af98b7d68ea4a7a 189 1 71.16 5f25063bd0fd1006d687a2565ec6964a 108 1 333.81 a7065fb28bf540beba112541b69f7925 215 1 34.69 361cfdd28b129a0d3ff26731e96e4e53 278 1 106.21 36516895f52da0be70add0bd202cae06 372 1 81.96 7e4bebe20140a71b34263a659ba1ce11 99 2 69.94 70154c8e9a3800762ea45dfff91108bf 365 1 149.69 c2495d0891221237c0146a60af8dd684 285 1 128.02 508723a71df892b7456450d4dede6e86 280 1 65.99 b44c8d45a4be6501f69e0e2d154ad06b 184 2 150.52 997871867623123ec99795f318b62c81 81 1 41.69 50b1d0db3c5c87be7d767f483e520263 284 1 136.94 5ef2199b05665d461d5e6fdd13f60f75 78 1 122.74 3d05f072d3052a4bb5adc28fab02ec4d 618 1 312.61 35b7ea3288096438f6dbe164d1f02aa0 416 1 110.21 c85df1c6ef6f7bb605e1c49d34f172ee 312 2 237.77 6fbee271a266c01a5f0f8cc10469a013 118 1 186.05 75905d0fe4b3c5ddb7740493c2c9304c 335 1 78.09 82e9bf33e750d1eb9d559d80fae0686b 250 1 46.14 4f2530392499792260517247376f3561 272 1 39.24 ec3127cf41d16e8ef977791aafcb9d44 531 1 151.53 bce006e903be688f122a39f45b210090 159 2 288.51 0fc53a0b4ce1b947356ebd10ed16e145 318 1 88.72 e533c359f12f908382cf31d51ef1e684 119 1 43.45 7fc3cdf9b7da8a526fde4bf5368d73c6 576 1 183.83 216ab90e27f18940cfac8f9f02fb4239 87 2 302.94 06130e682d8ee0cba49124f483ea3de0 548 1 62.34 59b265b9cfda8d25bbc84f722b90b139 551 1 315.26 a439177407290b4a5118b05ef53196e0 212 1 87.05 c20c61ce274e37eeb91b2e4e9e473c30 285 1 216.06 3f1c5888577d299fc92eb89ed8ffd381 310 1 387.67 71430416a809573ed4a01e04fa8e3b91 510 1 27.24 fcab9346a63e15349572e6f396f8b213 520 1 105.37 e36d108281c19ba00d15de8880a51b69 82 1 1210.62 95df5159db6002b35b9c645006abb4a7 363 2 921.04 8eb02bcfcb2deb1871afa092fbc732c9 154 1 65.81 87b2e4a2df8e1635a1f89705abb6e94b 562 1 67.95 958da6ff0122fa69bc5e1dc0e176abd9 427 1 73.34 5e5e45d10f0d852c85733ded028ab58e 89 1 72.58 0e1a29e5ec2a8b40b08f40c187d6add9 604 1 126.37 5a2e


## Ranking

 - **Classificação dos dados de acordo com quartis:** As colunas recency, frequency e value são classificadas de acordo com os quartis 25%, 50% e 75%, respectivamente. Isso significa que estamos dividindo os dados em quatro partes iguais com base em cada métrica.
 - **Classificação dos tiers com base no score: Os tiers (Bronze, Silver, Gold)** são atribuídos com base nos quartis calculados.

 O uso de quartis permite uma distribuição equitativa dos clientes em cada tier com base na distribuição dos dados.
____
 **Para melhoria:** O calculo de score deveria ser revisto. Por exemplo, clientes com alta frequência e alto valor são extremamente valiosos, enquanto aqueles com alta recência, mas baixa frequência e valor, podem precisar de mais atenção para aumentar seu engajamento. 


### quartiles

**Calcular os quartis das métricas RFV:**

Utilizamos a função approxQuantile para calcular os quartis das métricas "recency" (tempo desde a última compra), "frequency" (frequência de compras) e "value" (valor total gasto).

Os quartis são calculados nos percentis 25%, 50% e 75%, com uma precisão de 0.01.

**Extrair os quartis para cada métrica:**
Extraimos os quartis calculados para cada métrica (recency, frequency e value) e criamos colunas separados (recency_quartiles, frequency_quartiles e value_quartiles).

In [0]:
# Calcular os quartis das métricas RFV
quartiles = df.approxQuantile(
    ["recency", "frequency", "value"], [0.25, 0.5, 0.75], 0.01
)

# Extrair os quartis para cada métrica
recency_quartiles = quartiles[0]
frequency_quartiles = quartiles[1]
value_quartiles = quartiles[2]

# Adicionar os quartis como colunas no DataFrame
df_rfv = df.withColumn("recency_quartile",
                       when(col("recency") <= recency_quartiles[0], "Q1")
                       .when((col("recency") > recency_quartiles[0]) & (col("recency") <= recency_quartiles[1]), "Q2")
                       .when((col("recency") > recency_quartiles[1]) & (col("recency") <= recency_quartiles[2]), "Q3")
                       .otherwise("Q4"))

df_rfv = df_rfv.withColumn("frequency_quartile",
                            when(col("frequency") <= frequency_quartiles[0], "Q1")
                            .when((col("frequency") > frequency_quartiles[0]) & (col("frequency") <= frequency_quartiles[1]), "Q2")
                            .when((col("frequency") > frequency_quartiles[1]) & (col("frequency") <= frequency_quartiles[2]), "Q3")
                            .otherwise("Q4"))

df_rfv = df_rfv.withColumn("value_quartile",
                            when(col("value") <= value_quartiles[0], "Q1")
                            .when((col("value") > value_quartiles[0]) & (col("value") <= value_quartiles[1]), "Q2")
                            .when((col("value") > value_quartiles[1]) & (col("value") <= value_quartiles[2]), "Q3")
                            .otherwise("Q4"))


### Tier

**Classificar os tiers com bas enas frequencias:**

- Se a recency for Q1 (melhor), a frequency for Q4 (melhor) e a value for Q4 (melhor), o cliente recebe o tier Gold, indicando o melhor desempenho possível.
- Se a recency for Q2 (segunda-melhor), a frequency for Q4 (melhor) e a value for Q3 (segundo-melhor), o cliente também recebe o tier Gold, desepenho medio

a frequencia está sendo utilizada como se tivesse maior peso para um tier maior.

Para qualquer outro caso, o cliente recebe o tier Bronze, indicando um desempenho abaixo dos níveis de prata e ouro.

**Disclaimer** esse cálculo é fictício e não deve ser levado em consideração "ao pé da letra". Apenas serve de teste para mostrar a possibilidade de segmentação de clientes para campanhas de marketing, por exemplo.

In [0]:
# Classificar os tiers
df = df_rfv.withColumn("tier",
    when((col("recency_quartile") == "Q1") & (col("frequency_quartile") == "Q4") & (col("value_quartile") == "Q4"), "Gold")
    .when((col("recency_quartile") == "Q2") & (col("frequency_quartile") == "Q4") & (col("value_quartile") == "Q3"), "Gold")
    .when((col("recency_quartile") == "Q2") & (col("frequency_quartile") == "Q3") & (col("value_quartile") == "Q3"), "Silver")
    .when((col("recency_quartile") == "Q3") & (col("frequency_quartile") == "Q3") & (col("value_quartile") == "Q2"), "Silver")
    .otherwise("Bronze")
)

In [0]:
display(df)

customer_unique_id recency frequency value recency_quartile frequency_quartile value_quartile tier 969cdc8af5b07074766e79c1e6d76c24 163 1 134.66 Q1 Q1 Q3 Bronze f2a9bc9a1db05c873e1419654f747f9e 78 1 122.42 Q1 Q1 Q3 Bronze d0c5e56e04e886e73c79b3b71f0d6f0b 466 1 79.24 Q4 Q1 Q2 Bronze 5f03b965e26e79a371d229cfeeb578d7 484 1 54.0 Q4 Q1 Q1 Bronze 14a188558af6cd5bc222ca773d395a7f 224 2 245.14999999999998 Q2 Q4 Q4 Bronze ef1c2fafea5285a4bfb61386bc5e3154 58 1 235.84 Q1 Q1 Q4 Bronze d339ed835c9d8fd6b1e3c5cb60850bc5 614 1 262.1 Q4 Q1 Q4 Bronze 39d6e50625a51a618c2cf02a026231c1 433 1 66.74 Q4 Q1 Q2 Bronze 8d2fa65d968da66afc05f2e28250c9dc 225 1 150.91 Q2 Q1 Q3 Bronze d04921557f1cde4963c30a11dfb1719d 55 1 155.98 Q1 Q1 Q3 Bronze 8033f408bcb75134075db3eb60b49937 432 2 130.0 Q4 Q4 Q3 Bronze 9ea65227cfac84dd2778bc0315dd8f10 55 1 119.79 Q1 Q1 Q3 Bronze 2a6ef69674d6f28002c72b8d123b3a27 208 1 32.69 Q2 Q1 Q1 Bronze 308dfe5168e217902973b27e7c91f27e 93 1 117.79 Q1 Q1 Q3 Bronze 1d2435aa3b858d45c707c9fc25e18779 638 16 147.58 Q4 Q4 Q3 Bronze 538f20c5da86daf31ec285792b8b603f 468 1 72.84 Q4 Q1 Q2 Bronze 968436577c1e2073b28031261cb45a24 286 1 91.26 Q3 Q1 Q2 Bronze 1843cceebcc1e391249a2714facc8ba3 162 1 99.43 Q1 Q1 Q2 Bronze 86669cc06c6e824b3f2edfc2daef762e 111 1 61.36 Q1 Q1 Q1 Bronze c114c44566c2d172b520bc3c8785ffdf 526 1 1234.62 Q4 Q1 Q4 Bronze f13f6afa0bcce14330a5bcb6f1076904 119 1 236.07 Q1 Q1 Q4 Bronze 8c2c7fb3be4fc1669b8c1c6059db1207 522 1 41.91 Q4 Q1 Q1 Bronze 384ffc528dd30fd49eff3dda9f00ce86 173 1 61.69 Q2 Q1 Q1 Bronze 10aa79627a28350b5c121a124096cb18 470 1 46.01 Q4 Q1 Q1 Bronze 19fe66d478bfedfdcc743014d562b777 127 1 56.97 Q1 Q1 Q1 Bronze 09976ab240099cc26220384fa752e4f1 198 1 91.82 Q2 Q1 Q2 Bronze e2fa02776abcbf7246ffd18f58e120ea 588 1 189.62 Q4 Q1 Q4 Bronze dfe634d4b8e0678799178b6ec8e1b0ba 94 1 85.58 Q1 Q1 Q2 Bronze 61bf8e4656ece5791021786c756f1894 105 1 241.95 Q1 Q1 Q4 Bronze 65be6248a39942f9ab10da91280e2576 93 1 64.91 Q1 Q1 Q2 Bronze 7d27012b117e625faff580bec7cdf2e1 239 1 194.64 Q2 Q1 Q4 Bronze d242c2a33b19c5fab2ccf4f67dcaba86 163 1 397.7 Q1 Q1 Q4 Bronze f43b5eb3178b2129b9c4ea51024fcbd9 201 1 61.79 Q2 Q1 Q1 Bronze 39735e754fd0147ac6b0b910b710e6de 233 1 95.22 Q2 Q1 Q2 Bronze aadd69366d3b2ff8d40da4f079a4fcf7 266 1 109.5 Q2 Q1 Q3 Bronze 90c329efbf418634b40f4a2a75d9331e 428 1 240.76 Q4 Q1 Q4 Bronze f1eb09d2858a28f796484f8a9dfe2872 388 1 93.3 Q3 Q1 Q2 Bronze 04ebe7670da121a91344d0fd5547222f 255 1 31.28 Q2 Q1 Q1 Bronze dddcc50cec9aabfe44b26c136236db0a 427 1 176.78 Q4 Q1 Q3 Bronze 8b6afb5c9eb182373c656b34bf3383fc 603 1 30.75 Q4 Q1 Q1 Bronze 3195d6c23c9f61b0bcfae41d3fe8a3db 128 1 106.5 Q1 Q1 Q2 Bronze 9eedcaf541a8a393248b2017afecf694 370 1 149.7 Q3 Q1 Q3 Bronze 8e61d2d055f4865036e7d62b6739c255 134 1 77.99 Q1 Q1 Q2 Bronze 30cd4e5146e6f7b12f08bacaec791418 130 1 76.12 Q1 Q1 Q2 Bronze 02bab436d042d111ec4b7c67cfab8835 75 1 145.94 Q1 Q1 Q3 Bronze 1973beff39565594011f9a0ef66f923e 391 1 218.16 Q3 Q1 Q4 Bronze 1a6c2d0ed3299790cb718bb7981558c7 70 1 62.02 Q1 Q1 Q1 Bronze 1234ccd4e0b359525af98b7d68ea4a7a 189 1 71.16 Q2 Q1 Q2 Bronze 5f25063bd0fd1006d687a2565ec6964a 108 1 333.81 Q1 Q1 Q4 Bronze a7065fb28bf540beba112541b69f7925 215 1 34.69 Q2 Q1 Q1 Bronze 361cfdd28b129a0d3ff26731e96e4e53 278 1 106.21 Q3 Q1 Q2 Bronze 36516895f52da0be70add0bd202cae06 372 1 81.96 Q3 Q1 Q2 Bronze 7e4bebe20140a71b34263a659ba1ce11 99 2 69.94 Q1 Q4 Q2 Bronze 70154c8e9a3800762ea45dfff91108bf 365 1 149.69 Q3 Q1 Q3 Bronze c2495d0891221237c0146a60af8dd684 285 1 128.02 Q3 Q1 Q3 Bronze 508723a71df892b7456450d4dede6e86 280 1 65.99 Q3 Q1 Q2 Bronze b44c8d45a4be6501f69e0e2d154ad06b 184 2 150.52 Q2 Q4 Q3 Gold 997871867623123ec99795f318b62c81 81 1 41.69 Q1 Q1 Q1 Bronze 50b1d0db3c5c87be7d767f483e520263 284 1 136.94 Q3 Q1 Q3 Bronze 5ef2199b05665d461d5e6fdd13f60f75 78 1 122.74 Q1 Q1 Q3 Bronze 3d05f072d3052a4bb5adc28fab02ec4d 618 1 312.61 Q4 Q1 Q4 Bronze 35b7ea3288096438f6dbe164d1f02aa0 416 1 110.21 Q4 Q1 Q3 Bronze c85df1c6ef6f7bb605e1c49d34f172ee 312 2 237.77 Q3 Q4 Q4 Bronze 6fbee271a266c01a5f0f8cc10469a013


## Saving data

In [0]:
save_dataframe(df, format_mode="delta", table_name=tb_name, target_location=target_location, mode="overwrite")

[LOG] Saving olist_gold.customers_rfv delta on dbfs:/FileStore/delta/brazilian_ecommerce/olist_customers_rfv_dataset/gold... OK!



## create delta table

TODO: implementar UPSERT

o upsert serve para não precisar reescrever todos os dados, mas aproveitar do Delta para fazer um MERGE, caso um registro antigo tenha uma nova versão e INSERT para os dados que são novos

In [0]:
create_table(table_name=tb_name, target_location=target_location)

[LOG] Creating delta table olist_gold.customers_rfv on dbfs:/FileStore/delta/brazilian_ecommerce/olist_customers_rfv_dataset/gold... OK!


In [0]:
# exit para fechar a execução
dbutils.notebook.exit("OK")

In [0]:
%sql

select * from olist_gold.customers_rfv

customer_unique_id recency frequency value recency_quartile frequency_quartile value_quartile tier 969cdc8af5b07074766e79c1e6d76c24 163 1 134.66 Q1 Q1 Q3 Bronze f2a9bc9a1db05c873e1419654f747f9e 78 1 122.42 Q1 Q1 Q3 Bronze d0c5e56e04e886e73c79b3b71f0d6f0b 466 1 79.24 Q4 Q1 Q2 Bronze 5f03b965e26e79a371d229cfeeb578d7 484 1 54.0 Q4 Q1 Q1 Bronze 14a188558af6cd5bc222ca773d395a7f 224 2 245.14999999999998 Q2 Q4 Q4 Bronze ef1c2fafea5285a4bfb61386bc5e3154 58 1 235.84 Q1 Q1 Q4 Bronze d339ed835c9d8fd6b1e3c5cb60850bc5 614 1 262.1 Q4 Q1 Q4 Bronze 39d6e50625a51a618c2cf02a026231c1 433 1 66.74 Q4 Q1 Q2 Bronze 8d2fa65d968da66afc05f2e28250c9dc 225 1 150.91 Q2 Q1 Q3 Bronze d04921557f1cde4963c30a11dfb1719d 55 1 155.98 Q1 Q1 Q3 Bronze 8033f408bcb75134075db3eb60b49937 432 2 130.0 Q4 Q4 Q3 Bronze 9ea65227cfac84dd2778bc0315dd8f10 55 1 119.79 Q1 Q1 Q3 Bronze 2a6ef69674d6f28002c72b8d123b3a27 208 1 32.69 Q2 Q1 Q1 Bronze 308dfe5168e217902973b27e7c91f27e 93 1 117.79 Q1 Q1 Q3 Bronze 1d2435aa3b858d45c707c9fc25e18779 638 16 147.58 Q4 Q4 Q3 Bronze 538f20c5da86daf31ec285792b8b603f 468 1 72.84 Q4 Q1 Q2 Bronze 968436577c1e2073b28031261cb45a24 286 1 91.26 Q3 Q1 Q2 Bronze 1843cceebcc1e391249a2714facc8ba3 162 1 99.43 Q1 Q1 Q2 Bronze 86669cc06c6e824b3f2edfc2daef762e 111 1 61.36 Q1 Q1 Q1 Bronze c114c44566c2d172b520bc3c8785ffdf 526 1 1234.62 Q4 Q1 Q4 Bronze f13f6afa0bcce14330a5bcb6f1076904 119 1 236.07 Q1 Q1 Q4 Bronze 8c2c7fb3be4fc1669b8c1c6059db1207 522 1 41.91 Q4 Q1 Q1 Bronze 384ffc528dd30fd49eff3dda9f00ce86 173 1 61.69 Q2 Q1 Q1 Bronze 10aa79627a28350b5c121a124096cb18 470 1 46.01 Q4 Q1 Q1 Bronze 19fe66d478bfedfdcc743014d562b777 127 1 56.97 Q1 Q1 Q1 Bronze 09976ab240099cc26220384fa752e4f1 198 1 91.82 Q2 Q1 Q2 Bronze e2fa02776abcbf7246ffd18f58e120ea 588 1 189.62 Q4 Q1 Q4 Bronze dfe634d4b8e0678799178b6ec8e1b0ba 94 1 85.58 Q1 Q1 Q2 Bronze 61bf8e4656ece5791021786c756f1894 105 1 241.95 Q1 Q1 Q4 Bronze 65be6248a39942f9ab10da91280e2576 93 1 64.91 Q1 Q1 Q2 Bronze 7d27012b117e625faff580bec7cdf2e1 239 1 194.64 Q2 Q1 Q4 Bronze d242c2a33b19c5fab2ccf4f67dcaba86 163 1 397.7 Q1 Q1 Q4 Bronze f43b5eb3178b2129b9c4ea51024fcbd9 201 1 61.79 Q2 Q1 Q1 Bronze 39735e754fd0147ac6b0b910b710e6de 233 1 95.22 Q2 Q1 Q2 Bronze aadd69366d3b2ff8d40da4f079a4fcf7 266 1 109.5 Q2 Q1 Q3 Bronze 90c329efbf418634b40f4a2a75d9331e 428 1 240.76 Q4 Q1 Q4 Bronze f1eb09d2858a28f796484f8a9dfe2872 388 1 93.3 Q3 Q1 Q2 Bronze 04ebe7670da121a91344d0fd5547222f 255 1 31.28 Q2 Q1 Q1 Bronze dddcc50cec9aabfe44b26c136236db0a 427 1 176.78 Q4 Q1 Q3 Bronze 8b6afb5c9eb182373c656b34bf3383fc 603 1 30.75 Q4 Q1 Q1 Bronze 3195d6c23c9f61b0bcfae41d3fe8a3db 128 1 106.5 Q1 Q1 Q2 Bronze 9eedcaf541a8a393248b2017afecf694 370 1 149.7 Q3 Q1 Q3 Bronze 8e61d2d055f4865036e7d62b6739c255 134 1 77.99 Q1 Q1 Q2 Bronze 30cd4e5146e6f7b12f08bacaec791418 130 1 76.12 Q1 Q1 Q2 Bronze 02bab436d042d111ec4b7c67cfab8835 75 1 145.94 Q1 Q1 Q3 Bronze 1973beff39565594011f9a0ef66f923e 391 1 218.16 Q3 Q1 Q4 Bronze 1a6c2d0ed3299790cb718bb7981558c7 70 1 62.02 Q1 Q1 Q1 Bronze 1234ccd4e0b359525af98b7d68ea4a7a 189 1 71.16 Q2 Q1 Q2 Bronze 5f25063bd0fd1006d687a2565ec6964a 108 1 333.81 Q1 Q1 Q4 Bronze a7065fb28bf540beba112541b69f7925 215 1 34.69 Q2 Q1 Q1 Bronze 361cfdd28b129a0d3ff26731e96e4e53 278 1 106.21 Q3 Q1 Q2 Bronze 36516895f52da0be70add0bd202cae06 372 1 81.96 Q3 Q1 Q2 Bronze 7e4bebe20140a71b34263a659ba1ce11 99 2 69.94 Q1 Q4 Q2 Bronze 70154c8e9a3800762ea45dfff91108bf 365 1 149.69 Q3 Q1 Q3 Bronze c2495d0891221237c0146a60af8dd684 285 1 128.02 Q3 Q1 Q3 Bronze 508723a71df892b7456450d4dede6e86 280 1 65.99 Q3 Q1 Q2 Bronze b44c8d45a4be6501f69e0e2d154ad06b 184 2 150.52 Q2 Q4 Q3 Gold 997871867623123ec99795f318b62c81 81 1 41.69 Q1 Q1 Q1 Bronze 50b1d0db3c5c87be7d767f483e520263 284 1 136.94 Q3 Q1 Q3 Bronze 5ef2199b05665d461d5e6fdd13f60f75 78 1 122.74 Q1 Q1 Q3 Bronze 3d05f072d3052a4bb5adc28fab02ec4d 618 1 312.61 Q4 Q1 Q4 Bronze 35b7ea3288096438f6dbe164d1f02aa0 416 1 110.21 Q4 Q1 Q3 Bronze c85df1c6ef6f7bb605e1c49d34f172ee 312 2 237.77 Q3 Q4 Q4 Bronze 6fbee271a266c01a5f0f8cc10469a013